In [36]:
# To get smooth ani|mations
import matplotlib.pyplot as plt
plt.rcParams['animation.ffmpeg_path'] = '\\Users\\lukep\\ffmpeg\\ffmpeg-20200206-343ccfc-win64-static\\bin\\'
import matplotlib.animation as animation
import matplotlib as mpl
import ffmpeg
mpl.rc('animation', html='jshtml')

import pickle as pkl

import numpy as np

In [37]:
path = '../DATA/Single/frames_2.pkl'

In [38]:
def update_scene(num, frames, patch):
    patch.set_data(frames[num])
    return patch,

def plot_animation(frames, repeat=False, interval=40):
    fig = plt.figure()
    patch = plt.imshow(frames[0], vmin=0, vmax=200)
    plt.axis('off')
    anim = animation.FuncAnimation(
        fig, update_scene, fargs=(frames, patch),
        frames=len(frames), repeat=repeat, interval=interval)
    plt.close()
    return anim

In [41]:
frames = pkl.load( open(path, "rb" ) )
frames = np.array(frames)[0:400][:,:,:,0]*125

In [43]:
plot_animation(frames)

In [23]:
anim.save('output.gif', fps=4, writer='imagemagick')

MovieWriter imagemagick unavailable; trying to use <class 'matplotlib.animation.PillowWriter'> instead.


# Combine Policies

In [26]:
from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

import abc
import os
os.environ["CUDA_VISIBLE_DEVICES"]="-1"  
import tensorflow as tf
from tensorflow import keras
import numpy as np
from numpy.random import exponential
import random
import pandas as pd

# To get smooth ani|mations
import matplotlib.pyplot as plt


from tf_agents.environments import py_environment
from tf_agents.environments import tf_environment
from tf_agents.environments import tf_py_environment
from tf_agents.environments import utils
from tf_agents.specs import array_spec
from tf_agents.environments import wrappers
from tf_agents.environments import suite_gym
from tf_agents.trajectories import time_step as ts
from tf_agents.environments.wrappers import ActionRepeat
from tf_agents.environments import batched_py_environment
from tf_agents.environments import parallel_py_environment
from tf_agents.drivers.dynamic_step_driver import DynamicStepDriver

from collections import deque

# Disable GPU FOR NOW
from tf_agents.policies.random_tf_policy import RandomTFPolicy
from gym.wrappers import frame_stack

# Import Snake Environment
import sys
sys.path.insert(0, '../Snake_Emulator')
from Snake_v6 import Snake
from Snake_v6 import SnakeEnv# Import Snake Environment

env = SnakeEnv(BOARD_SIZE=8,
               MAX_HEALTH=100,
               FOOD_REWARD=1,
               DEATH_REWARD = -1,
               STEP_REWARD=0,
               REWARD_TYPE=3,
               FOOD_REWARD_TYPE=0,
               KILL_STEP_REWARD = 0,
               FOOD_SPAWN_MODE=1,
               MAX_COUNTER=3,
               HEALTH_CUTOFF=100,
              DRF_MC_HIGH=0,
              DRF_MC_LOW=0,
              IMMORTAL = False,
              WALL_PENALTY=0)
tf_env = tf_py_environment.TFPyEnvironment(env)
tf_env.reset()

TimeStep(step_type=<tf.Tensor: shape=(1,), dtype=int32, numpy=array([0], dtype=int32)>, reward=<tf.Tensor: shape=(1,), dtype=float32, numpy=array([0.], dtype=float32)>, discount=<tf.Tensor: shape=(1,), dtype=float32, numpy=array([1.], dtype=float32)>, observation=(<tf.Tensor: shape=(1, 8, 8, 2), dtype=int32, numpy=
array([[[[0, 0],
         [0, 0],
         [0, 0],
         [0, 0],
         [0, 0],
         [0, 0],
         [0, 0],
         [0, 0]],

        [[0, 0],
         [0, 0],
         [0, 0],
         [0, 0],
         [0, 0],
         [0, 0],
         [0, 0],
         [0, 0]],

        [[0, 0],
         [0, 0],
         [0, 0],
         [0, 0],
         [0, 0],
         [0, 0],
         [0, 0],
         [0, 0]],

        [[0, 0],
         [0, 0],
         [0, 0],
         [0, 0],
         [0, 0],
         [0, 0],
         [0, 0],
         [0, 0]],

        [[0, 0],
         [0, 0],
         [1, 1],
         [0, 0],
         [0, 0],
         [0, 0],
         [0, 0],
         [0,

Get video frames

In [33]:
def get_vid_frames(policy1, policy2, num_episodes=100, fps=2):
        frames = []
        for _ in range(num_episodes):
            time_step = tf_env.reset()
            frames.append(np.abs(env.get_board()))
            while not time_step.is_last():
                health = tf_env.current_time_step()[3][1].numpy()[0][0]
                if health<0.3:
                    action_step = policy1.action(time_step)
                else:
                    action_step = policy2.action(time_step)
                time_step = tf_env.step(action_step.action)
                frames.append(np.abs(env.get_board()))
        return frames

In [34]:
# hUNGRY
policy1 = tf.compat.v2.saved_model.load('../DATA/Single/policy_19')
# fULL
policy2 = tf.compat.v2.saved_model.load('../DATA/Single/policy_21')
frames = get_vid_frames(policy1, policy2, num_episodes=100, fps=2)

In [35]:
len(frames)

58745

In [32]:
frames = [255*np.insert(frame[0],2,0,axis=2) for frame in frames][0:2000]
plot_animation(frames)